In [1]:
import warnings
warnings.filterwarnings('ignore')

import sys
sys.path.append('../')

import plotly.express as px

from utils.path_utils import project_root
import IPython.display as ipd

import os
import pandas as pd
import numpy as np
from utils.path_utils import project_root
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import DBSCAN
from sklearn.neighbors import LocalOutlierFactor

from sklearn.manifold import TSNE
%matplotlib inline


In [3]:
train_data = pd.read_csv(os.path.join(project_root(), 'data', 'processed',
                                      'librispeech-gender-feats-train-clean-100.csv'))

dev_data = pd.read_csv(os.path.join(project_root(), 'data', 'processed',
                                    'librispeech-gender-feats-dev-clean.csv'))

data = dev_data.dropna()

# columns = ['mean', 'std', 'median', 'kurt', 'skew', 'p25', 'p75', 'iqr', 'ent', 'meanfun', 'maxfun', 'minfun']
columns = ['mean', 'std', 'median', 'kurt', 'skew', 'p25', 'p75', 'iqr', 'ent', 'meanfun']
cols = ['mean', 'std', 'median', 'kurt', 'skew', 'p25', 'p75', 'iqr', 'ent', 'meanfun', 'duration']

values = data[columns].values

clf = LocalOutlierFactor(n_neighbors=10) #, contamination=0.01
lof = clf.fit_predict(values)
lof_values = clf.negative_outlier_factor_
data['outlier'] = np.where(lof == -1, 'True', 'False')
data['lof_factor'] = lof_values
data['lof_factor'] = lof_values
data_sorted = data.sort_values('lof_factor')
print((data['outlier'].value_counts()))


perplexity = 20
tsne = TSNE(n_components=2, perplexity=perplexity, random_state=42)
feats2d = tsne.fit_transform(values)

data['y'] = feats2d[:, 1]
data['x'] = feats2d[:, 0]
fig = px.scatter(data, x='x', y='y', title=f'train data', color="outlier", hover_data=['path'], symbol='label', symbol_sequence=['star', 'diamond']);
fig.show()

False    2399
True      267
Name: outlier, dtype: int64


In [4]:
import soundfile as sf
root = os.path.join(project_root(), 'data', 'raw', 'LibriSpeech')

outliers = []
for i, row in enumerate(data_sorted['lof_factor']):
    if row < -1.5:
        path = data_sorted.iloc[i]['path']
        outliers.append([path, data_sorted.iloc[i]])
data_mean = data.mean()
data_3std = 3*data.std()
data_bottom = data_mean - data_3std 
data_top = data_mean + data_3std 


In [5]:
ind = 0

samples, fs = sf.read(os.path.join(root, outliers[ind][0]))
for col in cols:
    if np.abs(outliers[ind][1][col] - data_mean[col]) >  data_3std[col]:
        print(col, outliers[ind][1][col])
# ipd.display(pd.concat([outliers[ind][1], data_bottom, data_top], axis=1))

ipd.Audio(samples, rate=fs)


kurt 143.7831856973396
skew 8.997341205466581


In [6]:
ind = 1

samples, fs = sf.read(os.path.join(root, outliers[ind][0]))
for col in cols:
    if np.abs(outliers[ind][1][col] - data_mean[col]) >  data_3std[col]:
        print(col, outliers[ind][1][col])
# ipd.display(pd.concat([outliers[ind][1], data_bottom, data_top], axis=1))
ipd.Audio(samples, rate=fs)


duration 24.03


In [7]:
ind = 2

samples, fs = sf.read(os.path.join(root, outliers[ind][0]))
for col in cols:
    if np.abs(outliers[ind][1][col] - data_mean[col]) >  data_3std[col]:
        print(col, outliers[ind][1][col])
ipd.Audio(samples, rate=fs)

In [8]:
ind = 3

samples, fs = sf.read(os.path.join(root, outliers[ind][0]))
for col in cols:
    if np.abs(outliers[ind][1][col] - data_mean[col]) >  data_3std[col]:
        print(col, outliers[ind][1][col])
ipd.Audio(samples, rate=fs)


In [9]:
ind = 4

samples, fs = sf.read(os.path.join(root, outliers[ind][0]))
for col in cols:
    if np.abs(outliers[ind][1][col] - data_mean[col]) >  data_3std[col]:
        print(col, outliers[ind][1][col])
ipd.Audio(samples, rate=fs)

duration 31.7
